In [1]:
import plotly.graph_objs as go
import plotly.io as pio
pio.templates.default = 'plotly_white'
from scipy.optimize import curve_fit

import numpy as np

In [2]:
x = np.array([17.0, 17.1, 17.2, 17.3, 17.4, 17.5, 17.6, 17.7])
y = np.array([3.28, 4.47, 6.31, 9.33, 15.66, 25.75, 46.74, 75.75])

In [3]:
def func(x, a, b, c):
    return a * np.exp(b * x) + c

def approximated(x, y):
    popt, cov = curve_fit(func, x, y, maxfev=100000)
    a, b, c = popt
    return func(x, a, b, c), popt, cov

In [4]:
_, params, cov = approximated(x, y)

In [5]:
x_appr = np.linspace(16.8, 17.7, 10000)
y_appr = func(x_appr, *params)

In [6]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=x,
        y=y,
        mode='markers',
        marker=dict(symbol='x'),
        showlegend=False
    )
)


fig.add_trace(
    go.Scatter(
        x=x_appr,
        y=y_appr,
        showlegend=False
    )
)

fig.show()

In [7]:
f_acc = (y_appr / 6.31)**2

fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=x_appr,
        y=f_acc,
        showlegend=False
    )
)

fig.update_yaxes(type="log")

fig.show()

In [8]:
from statsmodels.stats.moment_helpers import cov2corr

A = 6.31
params_errors = np.sqrt(abs(cov.diagonal()))
corr_matrix = cov2corr(cov)
da = params_errors[0]
db = params_errors[1]
dc = params_errors[2]
a = params[0]
b = params[1]
c = params[2]
df_da = lambda x: 2 / A**2 * np.exp(b*x) * (a*np.exp(b*x) + c)
df_db = lambda x: 2 * a * x / A**2 * np.exp(b*x) * (a*np.exp(b*x) + c)
df_dc = lambda x: 2 / A**2 * (a*np.exp(b*x) + c)
delta_f = lambda x: (df_da(x)*da)**2 + (df_db(x)*db)**2 + (df_dc(x)*dc)**2 +\
                    2 * (
                         df_da(x)*df_db(x)*corr_matrix[0, 1]*da*db + 
                         df_da(x)*df_dc(x)*corr_matrix[0, 2]*da*dc +
                         df_db(x)*df_dc(x)*corr_matrix[1, 2]*db*dc
                        )

In [9]:
import pandas as pd

R = np.linspace(16.4, 17.2, 161)
f_acc = (func(R, *params) / A)**2
df = pd.DataFrame(f_acc, index=R, columns=['accidentals'])
df['accidentals_err'] = np.sqrt(delta_f(R))
df.to_csv(f'plots/fv/accidentals.csv', index=False)

In [10]:
df

accidentals  accidentals_err
16.400     0.038972         0.052091
16.405     0.039088         0.052145
16.410     0.039207         0.052200
16.415     0.039330         0.052257
16.420     0.039457         0.052315
...             ...              ...
17.180     0.824845         0.135982
17.185     0.861044         0.137675
17.190     0.899043         0.139422
17.195     0.938933         0.141226
17.200     0.980815         0.143094

[161 rows x 2 columns]